#### [ 가변 길이의 텍스트 처리를 위한 모델 ]  
- 임베딩층 : nn.EmbeddingBag  
- 구현
	* 입력 테스트의 길이를 측정해서 길이만큼 추출 후 진행

[1] 모듈 로딩 및 데이터 준비 <hr>

In [3]:
## 모듈로딩
import torch
import torch.nn as nn
from torchtext.datasets import AG_NEWS

In [4]:
## 데이터 준비
SAVE_DIR = '../data/'

[2] 데이터 로딩 및 확인 <hr>

In [6]:
## python의 torchtext의 내장 데이터셋
trainDS, testDS = AG_NEWS()

In [10]:
## 데이터 확인
for idx, (label, news) in enumerate(trainDS):
	print(label, news)
	
	if idx==10: break

3 Wall St. Bears Claw Back Into the Black (Reuters) Reuters - Short-sellers, Wall Street's dwindling\band of ultra-cynics, are seeing green again.
3 Carlyle Looks Toward Commercial Aerospace (Reuters) Reuters - Private investment firm Carlyle Group,\which has a reputation for making well-timed and occasionally\controversial plays in the defense industry, has quietly placed\its bets on another part of the market.
3 Oil and Economy Cloud Stocks' Outlook (Reuters) Reuters - Soaring crude prices plus worries\about the economy and the outlook for earnings are expected to\hang over the stock market next week during the depth of the\summer doldrums.
3 Iraq Halts Oil Exports from Main Southern Pipeline (Reuters) Reuters - Authorities have halted oil export\flows from the main pipeline in southern Iraq after\intelligence showed a rebel militia could strike\infrastructure, an oil official said on Saturday.
3 Oil prices soar to all-time record, posing new menace to US economy (AFP) AFP - Tearaway

In [11]:
for idx, (label, news) in enumerate(testDS):
	print(label, news)
	
	if idx==10: break

3 Fears for T N pension after talks Unions representing workers at Turner   Newall say they are 'disappointed' after talks with stricken parent firm Federal Mogul.
4 The Race is On: Second Private Team Sets Launch Date for Human Spaceflight (SPACE.com) SPACE.com - TORONTO, Canada -- A second\team of rocketeers competing for the  #36;10 million Ansari X Prize, a contest for\privately funded suborbital space flight, has officially announced the first\launch date for its manned rocket.
4 Ky. Company Wins Grant to Study Peptides (AP) AP - A company founded by a chemistry researcher at the University of Louisville won a grant to develop a method of producing better peptides, which are short chains of amino acids, the building blocks of proteins.
4 Prediction Unit Helps Forecast Wildfires (AP) AP - It's barely dawn when Mike Fitzpatrick starts his shift with a blur of colorful maps, figures and endless charts, but already he knows what the day will bring. Lightning will strike in places he e

[3] 데이터로더 생성 <hr>

In [34]:
## 관련 모듈 로딩
from torch.utils.data import DataLoader					## 데이터셋, 데이터로더 관련 모듈
from torch.nn.utils.rnn import pad_sequence				## 데이터 길이 맞추기 위한 패딩 함수 모듈

## 토커나이저, 단어사전 관련 모듈듈
from torchtext.data.utils import get_tokenizer			## 토커나이저 인스턴스 추출
from torchtext.vocab import build_vocab_from_iterator	## 데이터셋에서 단어사전 생성 함수
from nltk.corpus import stopwords						## 불용어 데이터셋

In [35]:
## ==> 특별 문자 토큰
UNK, PAD = '<UNK>', '<PAD>'
STOPWORDS = stopwords.words('english')
print(f'STOPWORDS : {STOPWORDS[:10]}')

## 토커나이즈 생성
tokenizer = get_tokenizer('basic_english')

STOPWORDS : ['a', 'about', 'above', 'after', 'again', 'against', 'ain', 'all', 'am', 'an']


In [36]:
## 토큰 제너레이더 함수 : 데이터 추출하여 토큰화
def yield_tokens(data_iter):
	for label, text in data_iter:
		# 라벨, 텍스트 => 텍스트 토큰화
		tokens = tokenizer(news)
		print(f'[tokens 1] => {len(tokens)}')
		tokens = [token for token in tokens if token not in STOPWORDS]
		print(f'[tokens 2] => {len(tokens)}')

		yield tokens

In [37]:
## => 단어사전 생성
vocab = build_vocab_from_iterator(
	yield_tokens(trainDS),
	specials = [PAD, UNK])

## 
vocab.set_default_index(vocab[PAD])

print(f'[vocab] {len(vocab)}개')

[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 64
[tokens 2] => 51
[tokens 1] => 

토큰화 => 단어/어휘 사전 생성

In [39]:
## 텍스트 >>> 정수 인코딩
text_pipeline = lambda x : vocab(tokenizer(x))

## 레이블 >>> 정수 인코딩
label_pipeline = lambda x : int(x) - 1

[3-2] 단어사전 생성 <hr>

In [40]:
## 배치크기만큼 데이터 로딩 시 위치 지정 위한 설정
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [46]:
### ===> DataLoader에서 배치크기만큼 데이터셋 반환 함수 
def collate_batch(batch):
    # 라벨, 뉴스, 뉴스기사 시작 위치 값 저장 변수 
    label_list, news_list, offsets = [], [], [0]
    
    # 배치에서 1개씩 샘플 즉, 피쳐와 라벨 추출 해서 저장 
    for label, news in batch:
         # 라벨 인코딩 후 추가 : 1 ~ 4 => 0 ~ 3
         label_list.append(label_pipeline(label))
         
         # 뉴스 기사 인코딩 후 저장
         processed_news = torch.tensor(text_pipeline(news), dtype=torch.int64)
         news_list.append(processed_news)
         
         ## 다음 뉴스를 읽기 위한 위치값 정보
         offsets.append(processed_news.size(0))
         print(f'news 토큰 수 => {processed_news.size(0)}개')
    
    # 배치 크기 만큼의 라벨 테스트 => 텐서화 진행     
    label_list = torch.tensor(label_list, dtype=torch.int64)

    # 배치 크기 만큼의 길이 위치값 => 텐서화 진행     
    offsets = torch.tensor(offsets[:-1]).cumsum(dim=0)
    # 배치 크기 만큼의 뉴스 기사 리스트 => 텐서화
    news_list = torch.cat(news_list)
    
    return label_list.to(DEVICE), news_list.to(DEVICE), offsets.to(DEVICE)

In [47]:
### => DataLoader 생성성
### ===> 학습용, 검증용, 테스트용 DataSet 준비 
BATCH_SIZE = 5

### 학습용, 검증용, 테스트용 Dataset, DataLoader 준비
trainDL = DataLoader(trainDS, 
					 batch_size=BATCH_SIZE, 
					 shuffle=True,
					 collate_fn=collate_batch )

testDL  = DataLoader(testDS,        
					 batch_size=BATCH_SIZE, 
					 shuffle=True, 
					 collate_fn=collate_batch )


In [48]:
## => 확인
cnt = 5
for label, news, offset in trainDL:
	print(f'\nlabels : {label.shape} => {label}')
	print(f'news 	 : {news.shape}')
	print(f'offset   : {offset}')
	cnt -= 1
	if cnt==0: break

news 토큰 수 => 46개
news 토큰 수 => 34개
news 토큰 수 => 68개
news 토큰 수 => 44개
news 토큰 수 => 43개

labels : torch.Size([5]) => tensor([0, 0, 2, 1, 2])
news 	 : torch.Size([235])
offset   : tensor([  0,  46,  80, 148, 192])
news 토큰 수 => 40개
news 토큰 수 => 44개
news 토큰 수 => 42개
news 토큰 수 => 47개
news 토큰 수 => 59개

labels : torch.Size([5]) => tensor([1, 3, 0, 2, 2])
news 	 : torch.Size([232])
offset   : tensor([  0,  40,  84, 126, 173])
news 토큰 수 => 45개
news 토큰 수 => 43개
news 토큰 수 => 54개
news 토큰 수 => 27개
news 토큰 수 => 33개

labels : torch.Size([5]) => tensor([2, 2, 2, 1, 3])
news 	 : torch.Size([202])
offset   : tensor([  0,  45,  88, 142, 169])
news 토큰 수 => 51개
news 토큰 수 => 59개
news 토큰 수 => 54개
news 토큰 수 => 54개
news 토큰 수 => 23개

labels : torch.Size([5]) => tensor([2, 3, 0, 2, 0])
news 	 : torch.Size([241])
offset   : tensor([  0,  51, 110, 164, 218])
news 토큰 수 => 53개
news 토큰 수 => 25개
news 토큰 수 => 46개
news 토큰 수 => 39개
news 토큰 수 => 37개

labels : torch.Size([5]) => tensor([2, 0, 2, 1, 2])
news 	 : torch.Size([2

c:\Users\KDP-35\anaconda3\envs\NLP\lib\site-packages\torch\utils\data\datapipes\iter\combining.py:337: UserWarning: Some child DataPipes are not exhausted when __iter__ is called. We are resetting the buffer and each child DataPipe will read from the start again.
  warnings.warn("Some child DataPipes are not exhausted when __iter__ is called. We are resetting "


[4] 모델 클래스 정의 및 설계 <hr>

In [ ]:
## --------------------------------------------------------
## 클래스이름 : TextModel
## 부모클래스 : Module
## 매개변수들 : 단어사전 갯수, 임베딩 수, 분류_클래스 갯수
## --------------------------------------------------------
class TextModel(nn.Module):
	## 모델층 정의 메서드
	def __init__(self, vocab_size, embed_dim, sparse=False):
		super().__init__()
		## 고차원 => 저차원
		self.embedding = nn.EmbeddingBag(vocab_size, embed_dim, sparse=False)
		